In [1]:
import numpy as np
import matplotlib.pyplot as plt
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from LXRfunc import load_dataset,masked_normalization
from LXRmodels import *

/home/test/anaconda3/envs/py3.6/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/test/anaconda3/envs/py3.6/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/test/anaconda3/envs/py3.6/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/test/anaconda3/envs/py3.6/lib/python3.6/site-pack

In [2]:
batch_size= 131
epochs = 400
dropout = 0.5
Rdropout_list = list(range(50,71,2))
Rdropout_list = [x/100 for x in Rdropout_list]
Rdropout_list

[0.5, 0.52, 0.54, 0.56, 0.58, 0.6, 0.62, 0.64, 0.66, 0.68, 0.7]

In [ ]:

for PCA_dim in range(24,31):
    reduced_dimension = PCA_dim
    X_train,y_train,X_test,y_test,num_classes = load_dataset('/home/test/Speech/X_training.csv','/home/test/Speech/y_training.csv','/home/test/Speech/X_testing.csv','/home/test/Speech/y_testing.csv',50,34,68,True)
    scaled_X_train,scaled_X_test = masked_normalization(X_train,X_test,scaler='ss')
    scaled_X_train = np.reshape(scaled_X_train,(-1,scaled_X_train.shape[2]))
    scaled_X_test = np.reshape(scaled_X_test,(-1,scaled_X_test.shape[2]))
    pca = PCA(n_components = reduced_dimension)
    pca.fit(scaled_X_train)
    scaled_X_train = pca.transform(scaled_X_train)
    scaled_X_test = pca.transform(scaled_X_test)
    X_train  = np.reshape(scaled_X_train,(X_train.shape[0],X_train.shape[1],reduced_dimension))
    X_test  = np.reshape(scaled_X_test,(X_test.shape[0],X_test.shape[1],reduced_dimension))
    X_train, X_test, y_train, y_test = train_test_split(X_train, y_train, test_size=0.2, random_state=6)

    for i in Rdropout_list:
        Rdropout = i 
        tf.keras.backend.clear_session()
        duo_bi_LSTM_his,yhat = duo_bi_LSTM_model(X_train,y_train,X_test,y_test,num_classes=num_classes,batch_size=batch_size,units=32,learning_rate=0.005,epochs=epochs,dropout = dropout,recurrent_dropout=Rdropout)
        tf.keras.backend.clear_session()
        trio_bi_LSTM_his,yhat = trio_bi_LSTM_model(X_train,y_train,X_test,y_test,num_classes=2,batch_size=batch_size,units=32,learning_rate=0.005,epochs=epochs,dropout=dropout,recurrent_dropout=Rdropout)
        tf.keras.backend.clear_session()
        quad_bi_LSTM_his,yhat = quad_bi_LSTM_model(X_train,y_train,X_test,y_test,num_classes=2,batch_size=batch_size,units=32,learning_rate=0.005,epochs=epochs,dropout=dropout,recurrent_dropout=Rdropout)
        tf.keras.backend.clear_session()
        trio_bi_LSTM_Dnn_his,yhat = trio_bi_LSTM_Dnn_model(X_train,y_train,X_test,y_test,num_classes=2,batch_size=batch_size,units=32,learning_rate=0.005,epochs=epochs,dropout=dropout,recurrent_dropout=Rdropout)
        tf.keras.backend.clear_session()
        trio_bi_LSTM_2Dnn_his,yhat = trio_bi_LSTM_2Dnn_model(X_train,y_train,X_test,y_test,num_classes=2,batch_size=batch_size,units=32,learning_rate=0.005,epochs=epochs,dropout=dropout,recurrent_dropout=Rdropout)
        fig = plt.figure(figsize=(14, 34))

        ax = fig.add_subplot(10,2,1)
        ax.plot(duo_bi_LSTM_his.history['acc'])
        ax.plot(duo_bi_LSTM_his.history['val_acc'])
        plt.hlines(0.75,2,400,'g')
        title = 'bi_duo'
        ax.title.set_text(title)

        ax = fig.add_subplot(10,2,2)
        ax.plot(trio_bi_LSTM_his.history['acc'])
        ax.plot(trio_bi_LSTM_his.history['val_acc'])
        plt.hlines(0.75,2,400,'g')
        title = 'bi_trio'
        ax.title.set_text(title)

        ax = fig.add_subplot(10,2,3)
        ax.plot(quad_bi_LSTM_his.history['acc'])
        ax.plot(quad_bi_LSTM_his.history['val_acc'])
        plt.hlines(0.75,2,400,'g')
        title = 'bi_quad'
        ax.title.set_text(title)

        ax = fig.add_subplot(10,2,4)
        ax.plot(trio_bi_LSTM_Dnn_his.history['acc'])
        ax.plot(trio_bi_LSTM_Dnn_his.history['val_acc'])
        plt.hlines(0.75,2,400,'g')
        title = 'trio_bi_LSTM_Dnn'
        ax.title.set_text(title)

        ax = fig.add_subplot(10,2,5)
        ax.plot(trio_bi_LSTM_2Dnn_his.history['acc'])
        ax.plot(trio_bi_LSTM_2Dnn_his.history['val_acc'])
        plt.hlines(0.75,2,400,'g')
        title = 'trio_bi_LSTM_2Dnn'
        ax.title.set_text(title)
        
        plt.suptitle('PCA dimension = {}, Dropout = {}, Recurrent_dropout = {}'.format(reduced_dimension,dropout,i),y=0.63)
        plt.xlabel('Epochs')
        plt.ylabel('acc')
        saving_path = '/home/test/Speech/Feature_engineering/plots/'+str(PCA_dim)+'Dim_'+str(i)+'RD.png'
        fig.savefig(saving_path)

load succeed
There are  2 classes
shape of X_train:  (655, 50, 34)
shape of X_test:  (91, 50, 34)
shape of y_train:  (655, 2)
shape of y_test:  (91, 2)
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
Train on 524 samples, validate on 131 samples
Epoch 1/400
524/524 [==============================] - 5s 9ms/sample - loss: 0.6904 - acc: 0.5229 - val_loss: 0.6908 - val_acc: 0.5344
Epoch 2/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6843 - acc: 0.5687 - v

/home/test/anaconda3/envs/py3.6/lib/python3.6/site-packages/ipykernel_launcher.py:27: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).


Train on 524 samples, validate on 131 samples
Epoch 1/400
524/524 [==============================] - 5s 10ms/sample - loss: 0.6900 - acc: 0.5477 - val_loss: 0.6969 - val_acc: 0.5191
Epoch 2/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6825 - acc: 0.5649 - val_loss: 0.7004 - val_acc: 0.5191
Epoch 3/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6790 - acc: 0.5687 - val_loss: 0.6913 - val_acc: 0.5115
Epoch 4/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6684 - acc: 0.5954 - val_loss: 0.6837 - val_acc: 0.5649
Epoch 5/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6669 - acc: 0.5992 - val_loss: 0.6840 - val_acc: 0.5802
Epoch 6/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6506 - acc: 0.6317 - val_loss: 0.6863 - val_acc: 0.5496
Epoch 7/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6458 - acc: 0.6393 - val_loss: 0.6898 - val_acc: 0.5496
Epoch 8/

/home/test/anaconda3/envs/py3.6/lib/python3.6/site-packages/ipykernel_launcher.py:27: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).


Train on 524 samples, validate on 131 samples
Epoch 1/400
524/524 [==============================] - 5s 9ms/sample - loss: 0.6836 - acc: 0.5534 - val_loss: 0.6993 - val_acc: 0.5191
Epoch 2/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6884 - acc: 0.5611 - val_loss: 0.6991 - val_acc: 0.5115
Epoch 3/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6687 - acc: 0.5763 - val_loss: 0.6943 - val_acc: 0.5115
Epoch 4/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6631 - acc: 0.5973 - val_loss: 0.6887 - val_acc: 0.5267
Epoch 5/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6348 - acc: 0.6622 - val_loss: 0.6903 - val_acc: 0.5420
Epoch 6/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6342 - acc: 0.6298 - val_loss: 0.7051 - val_acc: 0.5573
Epoch 7/400
524/524 [==============================] - 1s 1ms/sample - loss: 0.6059 - acc: 0.6908 - val_loss: 0.7162 - val_acc: 0.5802
Epoch 8/4